# Step 1: Import Necessary Libraries

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
from mediapipe_model_maker import gesture_recognizer
import tensorflow as tf
assert tf.__version__.startswith('2')
print("TensorFlow version:", tf.__version__)
print("CUDA version:", tf.sysconfig.get_build_info()["cuda_version"])
print("CuDNN version:", tf.sysconfig.get_build_info()["cudnn_version"])

2024-09-09 08:05:34.110751: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-09-09 08:05:34.166070: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-09-09 08:05:34.166116: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-09-09 08:05:34.167551: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-09-09 08:05:34.176380: I tensorflow/core/platform/cpu_feature_guar

TensorFlow version: 2.15.1
CUDA version: 12.2
CuDNN version: 8


# Step 2: Define Learning Rate Adjustment Functions

We'll now define the functions for each of the learning rate adjustment strategies.

## 2.1. Cosine Annealing

In [2]:
def cosine_annealing(epoch, total_epochs, initial_lr, min_lr=1e-6):
    """
    Cosine annealing learning rate schedule.

    Args:
        epoch (int): The current epoch.
        total_epochs (int): The total number of epochs for training.
        initial_lr (float): The initial learning rate.
        min_lr (float): The minimum learning rate.
    
    Returns:
        float: The updated learning rate for the current epoch.
    """
    return min_lr + (initial_lr - min_lr) * (1 + np.cos(np.pi * epoch / total_epochs)) / 2


## 2.2. Proportional Learning Rate Adjustment (based on loss and accuracy changes)

In [3]:
def adjust_learning_rate_proportional(lr, prev_loss, current_loss, prev_acc, current_acc, base_factor, acc_factor, min_lr=1e-6):
    """
    Dynamically adjust the learning rate based on loss and accuracy changes.

    Args:
        lr (float): The current learning rate.
        prev_loss (float): The loss from the previous epoch.
        current_loss (float): The loss from the current epoch.
        prev_acc (float): The accuracy from the previous epoch.
        current_acc (float): The accuracy from the current epoch.
        base_factor (float): Factor for loss-based adjustment.
        acc_factor (float): Factor for accuracy-based adjustment.
        min_lr (float): The minimum learning rate.
    
    Returns:
        float: The adjusted learning rate for the current epoch.
    """
    relative_loss_change = (prev_loss - current_loss) / prev_loss if prev_loss != 0 else 0
    relative_acc_change = (current_acc - prev_acc) / prev_acc if prev_acc != 0 else 0
    adjustment_factor = 1 + base_factor * relative_loss_change + acc_factor * relative_acc_change
    return max(lr * adjustment_factor, min_lr)


## 2.3. Adam-Based Learning Rate Adjustment

In [4]:
def adjust_learning_rate_adam(lr, loss, m, v, t, beta1=0.9, beta2=0.999, epsilon=1e-8):
    """
    Adjust the learning rate using Adam optimizer principles based on loss.

    Args:
        lr (float): The current learning rate.
        loss (float): The current loss.
        m (float): First moment vector (momentum).
        v (float): Second moment vector (variance).
        t (int): Time step or epoch.
        beta1 (float): Exponential decay rate for first moment estimates.
        beta2 (float): Exponential decay rate for second moment estimates.
        epsilon (float): Small constant for numerical stability.
    
    Returns:
        tuple: Adjusted learning rate, updated first moment (m), updated second moment (v), and updated time step (t).
    """
    t += 1
    m = beta1 * m + (1 - beta1) * loss
    v = beta2 * v + (1 - beta2) * (loss ** 2)
    m_hat = m / (1 - beta1 ** t)
    v_hat = v / (1 - beta2 ** t)
    adjusted_lr = lr / (np.sqrt(v_hat) + epsilon)
    return adjusted_lr, m, v, t


# Step 3: Define Training Functions for Each Strategy

We'll define functions that use each of these methods for training the model. These functions will accept training data, validation data, and other parameters, and will apply the learning rate adjustments in each epoch.
For each of these methods, a training function is implemented to log validation loss and accuracy, which will later be used for graph plotting.
## 3.1. Training with Adam-Based Learning Rate Adjustment

In [5]:
from mediapipe_model_maker import gesture_recognizer
from tqdm import tqdm

def train_with_adam_adjustment(train_data, validation_data, test_data, epochs, initial_lr, batch_size, export_dir):
    """
    Train the model using Adam-based learning rate adjustment, export the trained model, and print test loss and accuracy.
    
    Args:
        train_data: The training dataset.
        validation_data: The validation dataset.
        test_data: The testing dataset.
        epochs: Number of epochs to train.
        initial_lr: Initial learning rate.
        batch_size: Batch size for training.
        export_dir: Directory to save the exported model.
    
    Returns:
        Tuple of validation loss and accuracy.
    """
    m, v, t = 0, 0, 0  # Adam optimizer initialization
    val_losses = []
    val_accuracies = []

    for epoch in tqdm(range(epochs), desc="Training Progress", unit="epoch"):
        if epoch == 0:
            # Initial model creation and evaluation
            hparams = gesture_recognizer.HParams(
                export_dir=f"{export_dir}/adam_model_{epoch}",
                epochs=1,
                learning_rate=initial_lr,
                lr_decay=1.0,  
                num_gpus=1,
                batch_size=batch_size
            )
            options = gesture_recognizer.GestureRecognizerOptions(hparams=hparams)
            model = gesture_recognizer.GestureRecognizer.create(
                train_data=train_data, validation_data=validation_data, options=options
            )

            # Evaluate the initial model
            val_loss, val_acc = model.evaluate(validation_data, batch_size=batch_size)
            adjusted_lr, m, v, t = adjust_learning_rate_adam(initial_lr, val_loss, m, v, t)
        else:
            adjusted_lr, m, v, t = adjust_learning_rate_adam(adjusted_lr, val_loss, m, v, t)

        print(f"Epoch {epoch}, Adjusted Learning Rate: {adjusted_lr}")

        # Train with adjusted learning rate
        hparams.learning_rate = adjusted_lr
        model = gesture_recognizer.GestureRecognizer.create(
            train_data=train_data, validation_data=validation_data, options=options
        )

        # Evaluate model on validation data
        val_loss, val_acc = model.evaluate(validation_data, batch_size=batch_size)
        print(f"Epoch {epoch}, Validation Loss: {val_loss}, Validation Accuracy: {val_acc}")

        val_losses.append(val_loss)
        val_accuracies.append(val_acc)

    # Export the trained model
    model.export(export_dir)
    print(f"Adam-based model exported to {export_dir}")

    # Final evaluation on test data
    test_loss, test_acc = model.evaluate(test_data, batch_size=batch_size)
    print(f"Test Loss: {test_loss}, Test Accuracy: {test_acc}")

    return val_losses, val_accuracies


## 3.2. Training with Proportional Adjustment (Loss and Accuracy)

In [6]:
def train_with_proportional_adjustment(train_data, validation_data, test_data, epochs, initial_lr, base_adjustment_factor, batch_size, export_dir):
    """
    Train the model using proportional learning rate adjustment, export the trained model, and print test loss and accuracy.
    
    Args:
        train_data: The training dataset.
        validation_data: The validation dataset.
        test_data: The testing dataset.
        epochs: Number of epochs to train.
        initial_lr: Initial learning rate.
        base_adjustment_factor: Factor for loss-based learning rate adjustment.
        batch_size: Batch size for training.
        export_dir: Directory to save the exported model.
    
    Returns:
        Tuple of validation loss and accuracy.
    """
    learning_rate = initial_lr
    prev_loss = float('inf')  # Initialize previous loss
    val_losses = []
    val_accuracies = []

    for epoch in tqdm(range(epochs), desc="Training Progress", unit="epoch"):
        if epoch == 0:
            hparams = gesture_recognizer.HParams(
                export_dir=f"{export_dir}/proportional_model_{epoch}",
                epochs=1,
                learning_rate=initial_lr,
                lr_decay=1.0,
                num_gpus=1,
                batch_size=batch_size
            )
            options = gesture_recognizer.GestureRecognizerOptions(hparams=hparams)
            model = gesture_recognizer.GestureRecognizer.create(
                train_data=train_data, validation_data=validation_data, options=options
            )
            current_loss, _ = model.evaluate(validation_data, batch_size=batch_size)
            prev_loss = current_loss
        else:
            learning_rate = adjust_learning_rate_proportional(learning_rate, prev_loss, val_loss, base_adjustment_factor)

        print(f"Epoch {epoch}, Adjusted Learning Rate: {learning_rate}")

        hparams.learning_rate = learning_rate
        model = gesture_recognizer.GestureRecognizer.create(
            train_data=train_data, validation_data=validation_data, options=options
        )

        val_loss, val_acc = model.evaluate(validation_data, batch_size=batch_size)
        print(f"Epoch {epoch}, Validation Loss: {val_loss}, Validation Accuracy: {val_acc}")

        val_losses.append(val_loss)
        val_accuracies.append(val_acc)
        prev_loss = val_loss

    model.export(export_dir)
    print(f"Proportional model exported to {export_dir}")

    test_loss, test_acc = model.evaluate(test_data, batch_size=batch_size)
    print(f"Test Loss: {test_loss}, Test Accuracy: {test_acc}")

    return val_losses, val_accuracies


## 3.3. Training with Hybrid (Cosine Annealing + Proportional Adjustment)

In [7]:
def adjust_learning_rate_hybrid(lr, prev_loss, current_loss, base_factor, acc_factor, prev_acc, current_acc):
    """Adjust learning rate based on loss and accuracy changes."""
    relative_loss_change = (prev_loss - current_loss) / prev_loss if prev_loss != 0 else 0
    relative_acc_change = (current_acc - prev_acc) / prev_acc if prev_acc != 0 else 0
    adjustment_factor = 1 + base_factor * relative_loss_change + acc_factor * relative_acc_change
    return lr * adjustment_factor

def train_with_hybrid_adjustment(train_data, validation_data, test_data, epochs, initial_lr, base_adjustment_factor, acc_adjustment_factor, batch_size, export_dir):
    """
    Train the model using hybrid learning rate adjustment, export the trained model, and print test loss and accuracy.
    
    Args:
        train_data: The training dataset.
        validation_data: The validation dataset.
        test_data: The testing dataset.
        epochs: Number of epochs to train.
        initial_lr: Initial learning rate.
        base_adjustment_factor: Factor for loss-based adjustment.
        acc_adjustment_factor: Factor for accuracy-based adjustment.
        batch_size: Batch size for training.
        export_dir: Directory to save the exported model.
    
    Returns:
        Tuple of validation loss and accuracy.
    """
    learning_rate = initial_lr
    prev_loss = float('inf')
    prev_acc = 0.0
    val_losses = []
    val_accuracies = []

    for epoch in tqdm(range(epochs), desc="Training Progress", unit="epoch"):
        base_lr = cosine_annealing(epoch, epochs, initial_lr)
        learning_rate = adjust_learning_rate_hybrid(base_lr, prev_loss, val_loss, base_adjustment_factor, acc_adjustment_factor, prev_acc, val_acc)

        print(f"Epoch {epoch}, Adjusted Learning Rate: {learning_rate}")

        hparams = gesture_recognizer.HParams(
            export_dir=f"{export_dir}/hybrid_model_{epoch}",
            epochs=1,
            learning_rate=learning_rate,
            lr_decay=1.0,
            num_gpus=1,
            batch_size=batch_size
        )
        options = gesture_recognizer.GestureRecognizerOptions(hparams=hparams)
        model = gesture_recognizer.GestureRecognizer.create(
            train_data=train_data, validation_data=validation_data, options=options
        )

        val_loss, val_acc = model.evaluate(validation_data, batch_size=batch_size)
        print(f"Epoch {epoch}, Validation Loss: {val_loss}, Validation Accuracy: {val_acc}")

        val_losses.append(val_loss)
        val_accuracies.append(val_acc)
        prev_loss = val_loss
        prev_acc = val_acc

    model.export(export_dir)
    print(f"Hybrid model exported to {export_dir}")

    test_loss, test_acc = model.evaluate(test_data, batch_size=batch_size)
    print(f"Test Loss: {test_loss}, Test Accuracy: {test_acc}")

    return val_losses, val_accuracies


# Step 4: Plotting the Results

After training the models, results from each learning rate strategy are plotted for comparison.

In [8]:
def plot_results(results, strategy_names, epochs):
    """
    Plot validation accuracy and loss across epochs for different learning rate adjustment strategies.

    Args:
        results (dict): Dictionary containing the losses and accuracies of each strategy.
        strategy_names (list): List of names of the learning rate strategies.
        epochs (int): Number of epochs.
    """
    plt.figure(figsize=(14, 6))
    
    # Plot validation accuracy
    plt.subplot(1, 2, 1)
    for strategy in strategy_names:
        plt.plot(range(epochs), results[strategy]['accuracy'], label=f'{strategy} - Accuracy')
    plt.title('Validation Accuracy across Epochs')
    plt.xlabel('Epochs')
    plt.ylabel('Accuracy')
    plt.legend()
    
    # Plot validation loss
    plt.subplot(1, 2, 2)
    for strategy in strategy_names:
        plt.plot(range(epochs), results[strategy]['loss'], label=f'{strategy} - Loss')
    plt.title('Validation Loss across Epochs')
    plt.xlabel('Epochs')
    plt.ylabel('Loss')
    plt.legend()
    
    plt.tight_layout()
    plt.show()


# Step 5: Train Models with Different Methods

Once we have the functions defined, we can train the models using different learning rate adjustment methods.

In [9]:
# Timing and Dataset Processing using gesture_recognizer
import time

# Measure the time it takes to process the dataset
start_time = time.time()

dataset_path = 'small_dataset_72'

data = gesture_recognizer.Dataset.from_folder(
    dirname=dataset_path,
    hparams=gesture_recognizer.HandDataPreprocessingParams(
        shuffle=True, min_detection_confidence=0.65
    ),
)

end_time = time.time()
print(f"Total time for dataset processing: {end_time - start_time:.2f} seconds")

# Step 7: Split Dataset into Training, Validation, and Test Sets
train_data, rest_data = data.split(0.8)
validation_data, test_data = rest_data.split(0.5)

Using existing files at /tmp/model_maker/gesture_recognizer/palm_detection_full.tflite
Using existing files at /tmp/model_maker/gesture_recognizer/hand_landmark_full.tflite
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/forbid/22846_00023.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/motor/37004_00034.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/write/64061_00037.jpg


I0000 00:00:1725869144.793052   57107 task_runner.cc:85] GPU suport is not available: INTERNAL: ; RET_CHECK failure (mediapipe/gpu/gl_context_egl.cc:77) display != EGL_NO_DISPLAYeglGetDisplay() returned error 0x300c
INFO: Created TensorFlow Lite XNNPACK delegate for CPU.
W0000 00:00:1725869144.828933   60850 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1725869144.850602   60850 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
/opt/conda/lib/python3.11/site-packages/google/protobuf/symbol_database.py:55: UserWarning: SymbolDatabase.GetPrototype() is deprecated. Please use message_factory.GetMessageClass() instead. SymbolDatabase.GetPrototype() will be removed soon.
  warnings.warn('SymbolDatabase.GetPrototype() is deprecated. Please '


INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/next/38233_00028.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/brother/07936_00017.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/radio/45916_00024.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/last year/32282_00020.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/interest/30168_00077.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/april/03154_00083.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/vote/61993_00025.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/stubborn/55313_00049.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/today/58683_00027.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_72/bowling/07394_00043.jpg
INFO:tensorflow:Loading image /home/jovyan/work/yash/small_dataset_7

2024-09-09 08:21:23.579183: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:21:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-09 08:21:23.630295: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:21:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-09 08:21:23.630388: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:21:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-09 08:21:23.646762: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:21:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-09 08:21:23.646890: I external/local_xla/xla/stream_executor

Using existing files at /tmp/model_maker/gesture_recognizer/gesture_embedder
INFO:tensorflow:Load valid hands with size: 11413, num_label: 73, labels: none,amazing,april,assist,borrow,bowling,brother,challenge,comma,crazy,deposit,design,devil,each,enjoy,exact,famous,few,forbid,great,grow up,guitar,haircut,hit,hockey,impossible,influence,interest,japan,join,joy,kid,kneel,knock,last year,lazy,license,melt,mix,motor,name,never,next,obtain,organize,over,photographer,pray,pretty,queen,question,quick,radio,really,respect,sad,stubborn,sunrise,toast,today,type,ugly,upset,use,valley,verb,vote,while,white,write,yes,your,yourself.


INFO:tensorflow:Load valid hands with size: 11413, num_label: 73, labels: none,amazing,april,assist,borrow,bowling,brother,challenge,comma,crazy,deposit,design,devil,each,enjoy,exact,famous,few,forbid,great,grow up,guitar,haircut,hit,hockey,impossible,influence,interest,japan,join,joy,kid,kneel,knock,last year,lazy,license,melt,mix,motor,name,never,next,obtain,organize,over,photographer,pray,pretty,queen,question,quick,radio,really,respect,sad,stubborn,sunrise,toast,today,type,ugly,upset,use,valley,verb,vote,while,white,write,yes,your,yourself.


Total time for dataset processing: 965.93 seconds


In [ ]:
# Parameters
initial_learning_rate = 0.09
base_adjustment_factor = 0.085
accuracy_adjustment_factor = 0.085
epochs = 10
batch_size = 128

# Define export directory for models
export_dir = './trained_models'

results = {}

# Train with Adam-based adjustment and export the model
val_losses, val_accuracies = train_with_adam_adjustment(train_data, validation_data, test_data, epochs, initial_learning_rate, batch_size, export_dir)
results['Adam'] = {'loss': val_losses, 'accuracy': val_accuracies}

# Train with Proportional adjustment and export the model
val_losses, val_accuracies = train_with_proportional_adjustment(train_data, validation_data, test_data, epochs, initial_learning_rate, base_adjustment_factor, batch_size, export_dir)
results['Proportional'] = {'loss': val_losses, 'accuracy': val_accuracies}

# Train with Hybrid adjustment and export the model
val_losses, val_accuracies = train_with_hybrid_adjustment(train_data, validation_data, test_data, epochs, initial_learning_rate, base_adjustment_factor, accuracy_adjustment_factor, batch_size, export_dir)
results['Hybrid'] = {'loss': val_losses, 'accuracy': val_accuracies}

# Plot results
plot_results(results, ['Adam', 'Proportional', 'Hybrid'], epochs)


Training Progress:   0%|                                                                                                                                                                                           | 0/10 [00:00<?, ?epoch/s]

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 hand_embedding (InputLayer  [(None, 128)]             0         
 )                                                               
                                                                 
 batch_normalization (Batch  (None, 128)               512       
 Normalization)                                                  
                                                                 
 re_lu (ReLU)                (None, 128)               0         
                                                                 
 dropout (Dropout)           (None, 128)               0         
                                                                 
 custom_gesture_recognizer_  (None, 73)                9417      
 out (Dense)                                                     
                                                             

INFO:tensorflow:Training the models...
2024-09-09 08:21:55.638856: I external/local_xla/xla/service/service.cc:168] XLA service 0x7f80bcc2b490 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2024-09-09 08:21:55.638918: I external/local_xla/xla/service/service.cc:176]   StreamExecutor device (0): Quadro RTX 8000, Compute Capability 7.5
2024-09-09 08:21:55.646197: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:269] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2024-09-09 08:21:55.690243: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:454] Loaded cuDNN version 8907
I0000 00:00:1725870115.796879   63416 device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


     71/Unknown - 118s 2s/step - loss: 2.2821 - categorical_accuracy: 0.3407

2024-09-09 08:23:45.788715: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 1061471288397995930
2024-09-09 08:23:45.788807: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 9835603534296059051
2024-09-09 08:23:45.788840: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 9945439438703837858
2024-09-09 08:23:45.788851: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 14104907563332453090
2024-09-09 08:23:45.788861: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 4845991714552300664
2024-09-09 08:23:45.788871: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 15498618537885877040
2024-09-09 08:23:45.788882: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv i

...

2024-09-09 09:36:08.097137: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 15371332645496766479
2024-09-09 09:36:08.097231: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 17703561714767853495
Training Progress:  80%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊                                   | 8/10 [1:14:22<16:07, 483.59s/epoch]

Epoch 7, Validation Loss: 1.3750081062316895, Validation Accuracy: 0.546012282371521
Epoch 8, Adjusted Learning Rate: 0.000869588593535721
Model: "model_9"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 hand_embedding (InputLayer  [(None, 128)]             0         
 )                                                               
                                                                 
 batch_normalization_9 (Bat  (None, 128)               512       
 chNormalization)                                                
                                                                 
 re_lu_9 (ReLU)              (None, 128)               0         
                                                                 
 dropout_9 (Dropout)         (None, 128)               0         
                                                                 
 custom_gesture_recognizer_  (None, 73)             

INFO:tensorflow:Training the models...


Resuming from ./trained_models/adam_model_0/epoch_models/model-0001
     71/Unknown - 135s 2s/step - loss: 1.3088 - categorical_accuracy: 0.5467

2024-09-09 09:38:24.801526: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 14494585240189657406
2024-09-09 09:38:24.801621: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 6419000978534056050
2024-09-09 09:38:24.801634: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 14494585240189657406
2024-09-09 09:38:24.801644: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 6230953867132617424
2024-09-09 09:38:24.801654: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 8844414379575821512
2024-09-09 09:38:24.801663: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 10440917972511385356
2024-09-09 09:38:24.801673: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv 